In [1]:
import sys
from pathlib import Path

# Get the root directory of the project
project_root = Path("/home/lxz/scmamba/KCellFM_tutorial/cell_atlases").parent.parent
# project_root = Path(__file__).parent.parent
sys.path.append(str(project_root))
import os
os.environ['CUDA_LAUNCH_BLOCKING'] = '1'

In [2]:
import os
import pickle
import torch
import numpy as np
import pandas as pd
import pyarrow.parquet as pq
from torch.utils.data import Dataset, DataLoader
from tqdm import tqdm
from models.gene_tokenizer import GeneVocab
from models.model import MambaModel

/home/lxz/tools/anaconda3/envs/scgpt/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
# 配置参数
max_seq_len = 2049
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [4]:
class SingleParquetFileDataset(Dataset):
    """Read the dataset of a single parquet file"""
    def __init__(self, file_path):
        self.df = pq.read_table(file_path).to_pandas()
    
    def __len__(self):
        return len(self.df)
    
    def __getitem__(self, idx):
        row = self.df.iloc[idx]
        return {
            'X': torch.FloatTensor(row['X']),
            'cell_type': row['cell_type']
        }

In [5]:
def preprocess_batch(x_batch, feature_names, vocab, device):
    """Preprocess batch data into model input format"""
    batch_size = x_batch.size(0)
    values_tensor = torch.full((batch_size, max_seq_len), -2.0, device=device)
    src_tensor = torch.full((batch_size, max_seq_len), vocab["<pad>"], dtype=torch.long, device=device)
    padding_mask = torch.zeros((batch_size, max_seq_len), dtype=torch.bool, device=device)
    
    nonzero_mask = x_batch > 0
    nonzero_counts = nonzero_mask.sum(dim=1)
    
    for i in range(batch_size):
        nz_count = min(nonzero_counts[i], max_seq_len-1)
        nz_idx = torch.nonzero(x_batch[i])[:nz_count].squeeze()
        nz_values = x_batch[i][nz_idx]
        
        values_tensor[i, 0] = 0.0
        values_tensor[i, 1:1+nz_count] = nz_values
        
        genes = ["<cls>"] + [feature_names[idx] for idx in nz_idx.cpu().numpy()]
        genes += ["<pad>"] * (max_seq_len - len(genes))
        
        src_tensor[i] = torch.tensor([
            vocab[gene] if gene in vocab else vocab["<unk>"] for gene in genes
        ], device=device)
        
        padding_mask[i] = torch.tensor([gene == "<pad>" for gene in genes], device=device)
    
    return values_tensor, src_tensor, padding_mask

In [6]:
def evaluate_single_file(model, file_path, feature_names, vocab):
    """Evaluate individual files and return predicted results"""
    dataset = SingleParquetFileDataset(file_path)
    loader = DataLoader(
        dataset,
        batch_size=256,
        shuffle=False,
        num_workers=4,
        pin_memory=True
    )
    
    preds = []
    with torch.no_grad():
        for batch in tqdm(loader, desc=f"Processing {os.path.basename(file_path)}"):
            x = batch['X'].to(device, non_blocking=True)
            
            values, src, mask = preprocess_batch(x, feature_names, vocab, device)
            
            with torch.cuda.amp.autocast(enabled=True):
                outputs = model(src=src, values=values, src_key_padding_mask=mask)
            
            preds.append(outputs["cls_output"].argmax(dim=1).cpu().numpy())
    
    return np.concatenate(preds)  # 返回1 x n的预测数组

In [7]:
def load_model(model_path, vocab_path):
    """Load pre trained model and vocabulary list"""
    vocab = GeneVocab.from_file(vocab_path)
    model = MambaModel(
        ntoken=len(vocab), d_model=512, nhead=8, d_hid=512, nlayers=6,
        dropout=0.2, pad_token="<pad>", pad_value=-2,
        input_emb_style="continuous", cell_emb_style="cls"
    )
    # print(model.state_dict().keys()) 
    model.load_state_dict(torch.load(model_path, map_location=device))
    model.to(device)
    model.eval()
    return model, vocab

In [8]:
if __name__ == "__main__":
    # 1. Load dataset
    df = pd.read_parquet('/home/lxz/merlin_cxg_2023_05_15_sf-log1p_minimal/var.parquet')
    feature_names = df['feature_name'].tolist()
    
    # 2. Load model
    model, vocab = load_model(
        "/mnt/HHD16T/DATA/lxz/model_state/cell_cls_3loss_6layer_final.pth",
        "/home/lxz/scmamba/vocab.json"
    )
    
    # 3. Retrieve all test files (sorted by number)
    test_dir = "/mnt/HHD16T/DATA/lxz/sctab/merlin_cxg_2023_05_15_sf-log1p/test"
    # test_dir = "/home/lxz/merlin_cxg_2023_05_15_sf-log1p_minimal/test"
    test_files = sorted(
        [os.path.join(test_dir, f) for f in os.listdir(test_dir) if f.endswith('.parquet')],
        key=lambda x: int(os.path.basename(x).split('.')[1])
    )
    
    # 4. Generate all predicted results
    all_preds = np.array([], dtype=np.int64)
    for file_path in tqdm(test_files, desc="Processing all files"):
        preds = evaluate_single_file(model, file_path, feature_names, vocab)
        all_preds = np.concatenate([all_preds, preds])
    
    # 5. Save as pkl file (1 x n format)
    output_path = "/home/lxz/scmamba/PKL/mamba_predictions_3loss_6layer620.pkl"
    with open(output_path, 'wb') as f:
        pickle.dump(all_preds, f)
    
    print(f"\nThe predicted results have been saved to {output_path}")
    print(f"Total number of predicted samples: {len(all_preds)}")
    print(f"Shape of predicted results: {all_preds.shape}")  # Should output (n,)

Processing part.0.parquet:  31%|██████████████████████████████████████▊                                                                                     | 40/128 [01:15<02:14,  1.52s/it]


Processing part.0.parquet:  64%|███████████████████████████████████████████████████████████████████████████████▍                                            | 82/128 [02:19<01:09,  1.52s/it]


Processing part.0.parquet:  97%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▏   | 124/128 [03:22<00:06,  1.50s/it]


Processing part.1.parquet:  28%|██████████████████████████████████▉                                                                                         | 36/128 [00:54<02:19,  1.52s/it]


Processing part.1.parquet:  61%|███████████████████████████████████████████████████████████████████████████▌                                                | 78/128 [01:58<01:19,  1.58s/it]


...

Processing part.104.parquet:  34%|█████████████████████████████████████████▉                                                                                | 44/128 [01:09<02:05,  1.49s/it]


Processing part.104.parquet:  67%|█████████████████████████████████████████████████████████████████████████████████▉                                        | 86/128 [02:11<01:02,  1.49s/it]


Processing part.104.parquet: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 128/128 [03:14<00:00,  1.52s/it]


Processing all files: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 106/106 [6:09:41<00:00, 209.26s/it]



The predicted results have been saved to /home/lxz/scmamba/PKL/mamba_predictions_3loss_6layer620.pkl
Total number of predicted samples: 3448832
Shape of predicted results: (3448832,)
